In [ ]:
import sys
sys.path.insert(0, "../")
import time
import numpy as np
from pinn import *
from grad_stats import *

import matplotlib.pyplot as plt

import torch
import torch.nn as nn
from torch.autograd import grad
from torch.optim import Adam
from torch.optim.lr_scheduler import ExponentialLR, MultiStepLR

from tqdm import tqdm_notebook as tqdm 
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

In [ ]:
# experiment setup
lx=0
ly=0
rx=1
ry=1

seed   = 1
#omega = 6*np.pi

print("seed", seed)

def kg_equation(x,y):
    return x*np.cos(5*np.pi*y) + (x*y)**3

x = np.linspace(lx,rx, 100)
y = np.linspace(ly, ry, 100)


xx,yy = np.meshgrid(x,y)
u_sol = kg_equation(xx,yy)

X = np.vstack([xx.ravel(), yy.ravel()]).T
plt.imshow(u_sol, cmap="twilight", origin="lower",vmin=-1.5,vmax=1.5)
plt.colorbar()


def u(x):
    return x[:, 0:1] * np.cos(5 * np.pi * x[:, 1:2]) + (x[:, 1:2] * x[:, 0:1])**3

def u_tt(x):
    return - 25 * np.pi**2 * x[:, 0:1] * np.cos(5 * np.pi * x[:, 1:2]) + 6 * x[:,1:2] * x[:,0:1]**3

def u_xx(x):
    return np.zeros((x.shape[0], 1)) +  6 * x[:,0:1] * x[:,1:2]**3

def f(x, alpha=-1.0, beta=0.0, gamma=1.0, k=3.0):
    return u_tt(x) + alpha * u_xx(x) + beta * u(x) + gamma * u(x)**k


In [ ]:
def sampler(num_r=2500, num_b=100,lx=0,rx=1,ly=0,ry=1,seed=1):
    # generate training data
    x = np.linspace(lx, rx, 100)
    y = np.linspace(ly, ry, 100)
    xb = np.linspace(lx,rx,num_b)
    yb = np.linspace(ly,ry,num_b)
    
    xx,yy = np.meshgrid(x,y)
    
    X = np.vstack([xx.ravel(), yy.ravel()]).T


    # X boundaries
    lb   = lx*np.ones((yb.shape))
    rb   = rx*np.ones((yb.shape))
    Xlb  = np.vstack((lb,yb)).T
    Xrb  = np.vstack((rb,yb)).T
    UXlb = kg_equation(Xlb[:,0:1],Xlb[:,1:2])
    UXrb = kg_equation(Xrb[:,0:1],Xrb[:,1:2])

    # Y boundaries
    lb   = ly*np.ones((xb.shape))
    rb   = ry*np.ones((xb.shape))
    Ylb  = np.vstack((xb,lb)).T
    Yrb  = np.vstack((xb,rb)).T
    UYlb = kg_equation(Ylb[:,0:1],Ylb[:,1:2])
    UYrb = kg_equation(Yrb[:,0:1],Yrb[:,1:2])

    seedc = seed
    np.random.seed(seedc)
    torch.manual_seed(seedc)

    # training tensors
    idxs = np.random.choice(xx.size, num_r, replace=False)
    X_train = torch.tensor(X[idxs], dtype=torch.float32, requires_grad=True,device=device)
    X_rb = torch.tensor(Xrb, dtype=torch.float32, device=device)
    X_lb = torch.tensor(Xlb, dtype=torch.float32, device=device)
    Y_rb = torch.tensor(Yrb, dtype=torch.float32, device=device)
    Y_lb = torch.tensor(Ylb, dtype=torch.float32, requires_grad=True,device=device)
    # compute mean and std of training data
    X_mean = torch.tensor(np.mean(np.concatenate([X[idxs], Xrb, Xlb, Yrb, Ylb], 0), axis=0, keepdims=True), dtype=torch.float32, device=device)
    X_std  = torch.tensor(np.std(np.concatenate([X[idxs], Xrb, Xlb, Yrb, Ylb], 0), axis=0, keepdims=True), dtype=torch.float32, device=device)
    U_Train= torch.tensor(f(X[idxs]), dtype=torch.float32, requires_grad=True,device=device)
    U_X_rb = torch.tensor(UXrb, dtype=torch.float32, device=device).reshape(num_b,1)
    U_X_lb = torch.tensor(UXlb, dtype=torch.float32, device=device).reshape(num_b,1)
    U_Y_rb = torch.tensor(UYrb, dtype=torch.float32, device=device).reshape(num_b,1)
    U_Y_lb = torch.tensor(UYlb, dtype=torch.float32, requires_grad=True, device=device).reshape(num_b,1)
    

    return X_train, X_lb, X_rb, Y_lb, Y_rb, U_Train,U_X_lb, U_X_rb, U_Y_lb, U_Y_rb, X_mean, X_std


In [ ]:



def KG_res(uhat, data):
    poly = torch.ones_like(uhat)
    
    du = grad(outputs=uhat, inputs=data, 
              grad_outputs=torch.ones_like(uhat), create_graph=True)[0]
    
    dudx = du[:,0:1]
    dudy = du[:,1:2]
    
    dudxx = grad(outputs=dudx, inputs=data, 
              grad_outputs=torch.ones_like(uhat), create_graph=True)[0][:,0:1]
    dudyy = grad(outputs=dudy, inputs=data, 
              grad_outputs=torch.ones_like(uhat), create_graph=True)[0][:,1:2]
    
    xin = data[:,0:1]
    yin = data[:,1:2]
    
    
    
    residual = dudyy - dudxx + uhat**3
                
    return residual
def u_t(uhat, data):
    poly = torch.ones_like(uhat)
    
    du = grad(outputs=uhat, inputs=data, 
              grad_outputs=torch.ones_like(uhat), create_graph=True)[0]
    
    
    dudy = du[:,1:2]
    return dudy - 0*uhat
    

In [ ]:
def plot_function(lx,rx,ly,ry,u_sol,out,method,extras=None):
    methods=["W1 (uniform)","W2 (max_by_mean)","W3 (std)","W4 (mean+std)","W5 (mean*std)","W6 (kurtosis)"]
    plt.subplot(1,3,1)
    plt.imshow(u_sol, cmap="twilight", origin="lower",vmin=-1.0,vmax=1.5)
    plt.xticks(np.arange(0,101,50),np.linspace(lx,rx,3),fontsize=12)
    plt.yticks(np.arange(0,101,50),np.linspace(ly,ry,3),fontsize=12)
    plt.xlabel(r"$x$",fontsize=15)
    plt.ylabel(r"$y$",fontsize=15)
    plt.title("Ground Truth",fontsize=18)
    plt.colorbar(fraction=0.046, pad=0.04)

    plt.subplot(1,3,2)
    plt.imshow(out, cmap="twilight", origin="lower",vmin=-1.0,vmax=1.5)
    plt.xticks(np.arange(0,101,50),np.linspace(lx,rx,3),fontsize=12)
    plt.yticks(np.arange(0,101,50),np.linspace(ly,ry,3),fontsize=12)
    plt.xlabel(r"$x$",fontsize=15)
    plt.ylabel(r"$y$",fontsize=15)
    plt.title("Prediction",fontsize=18)
    plt.colorbar(fraction=0.046, pad=0.04)

    plt.subplot(1,3,3)
    plt.imshow(np.abs(out-u_sol)/np.max(np.abs(u_sol)), cmap="nipy_spectral", origin="lower",vmin=0,vmax=0.2)
    plt.xticks(np.arange(0,101,50),np.linspace(lx,rx,3),fontsize=12)
    plt.yticks(np.arange(0,101,50),np.linspace(ly,ry,3),fontsize=12)
    plt.xlabel(r"$x$",fontsize=15)
    plt.ylabel(r"$y$",fontsize=15)
    plt.title("Point-wise Error",fontsize=18)
    plt.colorbar(fraction=0.046, pad=0.04)
    
    
    
    plt.gcf().set_size_inches(15,5)
    plt.tight_layout()
    plt.suptitle("Klein-Gordon Equation using PINN_{}".format(methods[method]),fontsize=25)
    plt.savefig(extras+"KGEqn_{}_based_Tanh".format(methods[method]),dpi=800)
    return None

In [ ]:
losses_boundary_global=[]
losses_residual_global=[]
lambdas_global=[]
list_of_l2_Errors=[]
for i in range(6):
    for j in range(5):
        sets = [[300,25],[500,25],[600,30],[750,50],[1000,100]]
        mm         = 5
        alpha_ann  = 0.5
        n_epochs   = 40001
        method = i
        num_r= sets[j][0]
        num_b= sets[j][1]
        extras=str(num_r)+ "+"+ str(num_b)
        print("#######Training with#####\n",extras)
        #print(extras)
        X_train, X_lb, X_rb, Y_lb, Y_rb, U_Train,U_X_lb, U_X_rb, U_Y_lb, U_Y_rb, X_mean, X_std= sampler(num_r,num_b,lx,rx,ly,ry,seed=1)
        net = PINN(sizes=[2,50,50,50,50,50,1], mean=X_mean, std=X_std, seed=1, activation=torch.nn.Tanh()).to(device)
        lambd       = 1
        lambds      = [];
        losses_boundary  = [];
        losses_residual = [];
        params = [{'params': net.parameters(), 'lr': 1e-5}]
        #milestones = [[10000,20000,30000]]
        optimizer = Adam(params)
        #scheduler = MultiStepLR(optimizer, milestones[0], gamma=0.1)
        print("training with shape", X_train.size())
        start_time = time.time()
        for epoch in range(n_epochs):     
            uhat  = net(X_train)
            res   = KG_res(uhat, X_train)
            l_reg = torch.mean((res-U_Train)**2)
            predl = net(X_lb)
            predr = net(X_rb)
            l_bc  = torch.mean((predl - U_X_lb)**2, dim=0)
            l_bc += torch.mean((predr - U_X_rb)**2, dim=0)
            predl = net(Y_lb)
            #predr = net(Y_rb)
            l_bc += torch.mean((predl - U_Y_lb)**2, dim=0)
            #l_bc += torch.mean((predr - U_Y_rb)**2, dim=0)    
            gpreds=u_t(predl,Y_lb)
            l_bc += torch.mean((gpreds)**2)
            with torch.no_grad():
                if epoch % mm == 0:
                    stdr,kurtr=loss_grad_stats(l_reg, net)
                    stdb,kurtb=loss_grad_stats(l_bc, net)
                    maxr,meanr=loss_grad_max_mean(l_reg, net)
                    maxb,meanb=loss_grad_max_mean(l_bc, net,lambg=lambd)
                    if method == 2:
                        # inverse dirichlet
                        lamb_hat = stdr/stdb
                        lambd     = (1-alpha_ann)*lambd + alpha_ann*lamb_hat
                        if lambd < 1:
                            lambd = torch.tensor(1.0, dtype=torch.float32, device=device)
                       
                    elif method == 1:
                        # max/avg
                        lamb_hat = maxr/meanb
                        lambd     = (1-alpha_ann)*lambd + alpha_ann*lamb_hat 
                        if lambd < 1:
                            lambd = torch.tensor(1.0, dtype=torch.float32, device=device)
            
                    elif method==3:
                        # mean + std weighing
                        covr= stdr + maxr
                        covb= stdb + meanb
                        lamb_hat = covr/covb
                        lambd     = (1-alpha_ann)*lambd + alpha_ann*lamb_hat
                        if lambd < 1:
                            lambd = torch.tensor(1.0, dtype=torch.float32, device=device)
            
                    elif method == 5:
                        # kurtosis based weighing
                        covr= stdr/kurtr
                        covb= stdb/kurtb
                        lamb_hat = covr/covb
                        lambd     = (1-alpha_ann)*lambd + alpha_ann*lamb_hat
                        if lambd < 1:
                            lambd = torch.tensor(1.0, dtype=torch.float32, device=device)
            
                    elif method == 4:
                        # mean * std weighing
                        covr= stdr * meanr
                        covb= stdb * meanb
                        lamb_hat = covr/covb
                        lambd     = (1-alpha_ann)*lambd + alpha_ann*lamb_hat
                        if lambd < 1:
                            lambd = torch.tensor(1.0, dtype=torch.float32, device=device)
            
                    else:
                        # uniform weighing 
                        lambd = 1;
            if(method == 0):
                loss = l_reg + l_bc
            elif(method == 1 or method == 2 or method==3 or method==4 or method == 5):
                loss = l_reg + lambd*l_bc
            if epoch%100==0:
                losses_boundary.append(l_bc.item())
                losses_residual.append(l_reg.item())
                if method !=0:
                    lambds.append(lambd.item())
            optimizer.zero_grad()
            loss.backward()
            optimizer.step()
            #scheduler.step()
            print("epoch {}/{}, loss={:.10f}, lambda={:.4f}, lr={:,.5f}\t\t\t"
                  .format(epoch+1, n_epochs, loss.item(), lambd, optimizer.param_groups[0]['lr']), end="\r")
        elapsed_time = time.time() - start_time
        #print('CPU time = ',elapsed_time)
        inp = torch.tensor(X, dtype=torch.float32, device=device)
        out = net(inp).cpu().data.numpy().reshape(u_sol.shape)
        print("\n.....\n")
        print("Method:",method)
        print("pred rel. l2-error = {:e}".format(np.linalg.norm(out.reshape(-1)-u_sol.reshape(-1))/np.linalg.norm(out.reshape(-1))))
        print("\n.....\n")
        if j==0:
            plot_function(lx,rx,ly,ry,u_sol,out,method,extras=extras)
        list_of_l2_Errors.append(np.linalg.norm(out.reshape(-1)-u_sol.reshape(-1))/np.linalg.norm(out.reshape(-1)))
        losses_boundary_global.append(losses_boundary)
        losses_residual_global.append(losses_residual)

In [ ]:
def split(list_a, chunk_size):

  for i in range(0, len(list_a), chunk_size):
    yield list_a[i:i + chunk_size]
List = list(split(list_of_l2_Errors,5))
for i in List:
    arr = np.array(i)
    #print("\n")
    print(arr)